# ipygany

[ipygany](https://ipygany.readthedocs.io/en/latest/) is a library that allows client side GPU rendering. This is useful because the data is sotred on the server and manipulations of the visualisation are near realtime.

This example:
1. Imports a netcdf file using xarray
1. Converts the netcdf file to a pyvista structured mesh
1. Converts the pyvista mesh to ipygany mesh
1. Colors and warps the mesh
1. Shows the interaction

## Imports

In [1]:
import pyvista as pv
import numpy as np
import xarray as xr

from ipygany import PolyMesh, Scene, IsoColor, WarpByScalar, ColorBar, colormaps
from ipywidgets import VBox, FloatSlider, FileUpload, Dropdown, jslink

## Data upload

In [2]:
# Create file upload
# To load several files press shift with selecting - 
#all the files have to be selected at the same time.

file_upload = FileUpload(multiple=False)
file_upload

FileUpload(value={}, description='Upload')

In [3]:
ds = xr.open_dataset(file_upload.data[0])
ds

<xarray.Dataset>
Dimensions:  (lat: 180, lon: 360)
Coordinates:
  * lon      (lon) float64 -179.5 -178.5 -177.5 -176.5 ... 177.5 178.5 179.5
  * lat      (lat) float64 -89.5 -88.5 -87.5 -86.5 -85.5 ... 86.5 87.5 88.5 89.5
Data variables:
    TOPO     (lat, lon) float32 ...
Attributes:
    history:  Created with add_noise.ncl -- 08.06.21 JBL

## Create pyvista structured mesh

In [4]:
xx, yy, zz = np.meshgrid(np.radians(ds['lon']), 
                         np.radians(ds['lat']), 
                         [0])

# Transform to spherical coordinates
radius = 6371.0e6
x = radius * np.cos(yy) * np.cos(xx)
y = radius * np.cos(yy) * np.sin(xx)
z = radius * np.sin(yy)

grid = pv.StructuredGrid(x, y, z)

# Add data to mesh
for var in ds.data_vars:
    grid[var] = np.array(ds[var]).ravel(order='F')

## Convert pyvista mesh to ipygany mesh

In [5]:
# Turn the PyVista mesh into a PolyMesh
mesh = PolyMesh.from_vtk(grid)

# Color the mesh
colored_mesh = IsoColor(mesh, min=ds.TOPO.min(), max=ds.TOPO.max())
# setup warping
warped_mesh = WarpByScalar(colored_mesh, input='TOPO', factor=0)

In [6]:
# Link a slider to the warp value
warp_slider = FloatSlider(min=0., max=10., value=0)

def on_slider_change(change):
    warped_mesh.factor = change['new'] * -10000

warp_slider.observe(on_slider_change, 'value')

# Create a colorbar widget
colorbar = ColorBar(colored_mesh)

# Colormap choice widget
colormap = Dropdown(
    options=colormaps,
    description='colormap:'
)

jslink((colored_mesh, 'colormap'), (colormap, 'index'))

VBox((colormap, warp_slider, Scene([warped_mesh])))